# INSTALL AND IMPORT

In [15]:
!pip install pytest-shutil

In [1]:
!pip install nibabel pydicom numpy

  Using cached importlib_resources-6.4.5-py3-none-any.whl (36 kB)


In [14]:
!pip install SimpleITK

In [12]:
!pip install --upgrade pydicom


In [4]:
import os
import glob

input_root_dir = r"D:\Task03_Liver\imagesTr"

# Support .nii and .nii.gz files
nifti_files = glob.glob(os.path.join(input_root_dir, "**", "*.nii*"), recursive=True)

if len(nifti_files) == 0:
    print("No NIfTI files found. Check your path and file extensions.")
else:
    print(f"✅ Found {len(nifti_files)} NIfTI files.")
    print(nifti_files[:5])  # Print first 5 file paths to verify detection


✅ Found 131 NIfTI files.
['D:\\Task03_Liver\\imagesTr\\liver_0.nii.gz', 'D:\\Task03_Liver\\imagesTr\\liver_1.nii.gz', 'D:\\Task03_Liver\\imagesTr\\liver_10.nii.gz', 'D:\\Task03_Liver\\imagesTr\\liver_100.nii.gz', 'D:\\Task03_Liver\\imagesTr\\liver_101.nii.gz']


In [4]:
from glob import glob
import shutil
import os
import dicom2nifti
import nibabel

# NIFTI TO DICOM (IMAGES)

In [26]:
import os
import glob
import nibabel as nib
import numpy as np
import pydicom
from pydicom.dataset import Dataset, FileDataset
import datetime

def nifti_to_dicom(nifti_path, dicom_output_path):
    """
    Convert a NIfTI image to DICOM slices and save in dicom_output_path.
    """
    # Load NIfTI image
    nii_img = nib.load(nifti_path)
    data = nii_img.get_fdata()
    dims = data.shape  # (X, Y, Z)

    os.makedirs(dicom_output_path, exist_ok=True)

    for i in range(dims[2]):  # Iterate over Z-axis (slices)
        slice_data = data[:, :, i]
        
        # Normalize to 16-bit grayscale
        slice_data_normalized = ((slice_data - np.min(slice_data)) /
                                 (np.max(slice_data) - np.min(slice_data)) * 65535).astype(np.uint16)
        
        # Create DICOM dataset
        file_meta = Dataset()
        ds = FileDataset(None, {}, file_meta=file_meta, preamble=b"\0" * 128)

        # Set metadata
        ds.PatientName = "Liver_Patient"
        ds.PatientID = os.path.basename(nifti_path).split(".")[0]
        ds.Modality = "CT"
        ds.StudyInstanceUID = pydicom.uid.generate_uid()
        ds.SeriesInstanceUID = pydicom.uid.generate_uid()
        ds.SOPInstanceUID = pydicom.uid.generate_uid()
        ds.StudyDate = datetime.datetime.now().strftime("%Y%m%d")
        ds.ContentDate = datetime.datetime.now().strftime("%Y%m%d")
        ds.ContentTime = datetime.datetime.now().strftime("%H%M%S")
        ds.Rows, ds.Columns = slice_data.shape

        # Pixel Data
        ds.SamplesPerPixel = 1
        ds.PhotometricInterpretation = "MONOCHROME2"
        ds.PixelRepresentation = 0
        ds.BitsAllocated = 16
        ds.BitsStored = 16
        ds.HighBit = 15
        ds.PixelData = slice_data_normalized.tobytes()
        ds.InstanceNumber = i + 1
        ds.SliceThickness = 1.0
        ds.ImagePositionPatient = [0, 0, i]
        ds.ImageOrientationPatient = [1, 0, 0, 0, 1, 0]
        ds.PixelSpacing = [1.0, 1.0]
        
        # Save DICOM file
        dicom_file_path = os.path.join(dicom_output_path, f"slice_{i:03d}.dcm")
        pydicom.dcmwrite(dicom_file_path, ds)
    
    print(f"✅ {os.path.basename(nifti_path)} converted: {dims[2]} DICOM slices saved to {dicom_output_path}")

def process_nifti_directory(input_root, output_root):
    """
    Process all NIfTI files in input_root and convert them to DICOM format.
    """
    nifti_files = glob.glob(os.path.join(input_root, "*.nii.gz"))
    print(f"Found {len(nifti_files)} NIfTI files.")
    
    for nifti_file in nifti_files:
        file_name = os.path.basename(nifti_file).split(".")[0]
        dicom_folder = os.path.join(output_root, file_name)
        print(f"Processing {nifti_file} --> {dicom_folder}")
        nifti_to_dicom(nifti_file, dicom_folder)
    
    print("🎯 All files processed successfully!")

# Set paths
input_root_dir = r"D:\\Task03_Liver\\imagesTr"  # Input NIfTI folder
output_root_dir = r"D:\\Task03_Liver\\dicomm_files\\images"  # Output DICOM folder

# Ensure paths are accessible
if not os.path.exists(input_root_dir):
    raise FileNotFoundError(f"Input directory does not exist: {input_root_dir}")

# Run conversion
process_nifti_directory(input_root_dir, output_root_dir)


Found 131 NIfTI files.
Processing D:\\Task03_Liver\\imagesTr\liver_0.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_0
✅ liver_0.nii.gz converted: 75 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_0
Processing D:\\Task03_Liver\\imagesTr\liver_1.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_1
✅ liver_1.nii.gz converted: 123 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_1
Processing D:\\Task03_Liver\\imagesTr\liver_10.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_10
✅ liver_10.nii.gz converted: 501 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_10
Processing D:\\Task03_Liver\\imagesTr\liver_100.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_100
✅ liver_100.nii.gz converted: 685 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_100
Processing D:\\Task03_Liver\\imagesTr\liver_101.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_101
✅ liver_101.nii.gz converted: 683 DICO

✅ liver_16.nii.gz converted: 689 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_16
Processing D:\\Task03_Liver\\imagesTr\liver_17.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_17
✅ liver_17.nii.gz converted: 826 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_17
Processing D:\\Task03_Liver\\imagesTr\liver_18.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_18
✅ liver_18.nii.gz converted: 845 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_18
Processing D:\\Task03_Liver\\imagesTr\liver_19.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_19
✅ liver_19.nii.gz converted: 547 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_19
Processing D:\\Task03_Liver\\imagesTr\liver_2.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_2
✅ liver_2.nii.gz converted: 517 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_2
Processing D:\\Task03_Liver\\imagesTr\liver_20.nii.gz --> D:\\Tas

✅ liver_52.nii.gz converted: 237 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_52
Processing D:\\Task03_Liver\\imagesTr\liver_53.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_53
✅ liver_53.nii.gz converted: 105 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_53
Processing D:\\Task03_Liver\\imagesTr\liver_54.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_54
✅ liver_54.nii.gz converted: 96 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_54
Processing D:\\Task03_Liver\\imagesTr\liver_55.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_55
✅ liver_55.nii.gz converted: 192 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_55
Processing D:\\Task03_Liver\\imagesTr\liver_56.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_56
✅ liver_56.nii.gz converted: 239 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_56
Processing D:\\Task03_Liver\\imagesTr\liver_57.nii.gz --> D:\\

✅ liver_89.nii.gz converted: 766 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_89
Processing D:\\Task03_Liver\\imagesTr\liver_9.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_9
✅ liver_9.nii.gz converted: 549 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_9
Processing D:\\Task03_Liver\\imagesTr\liver_90.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_90
✅ liver_90.nii.gz converted: 751 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_90
Processing D:\\Task03_Liver\\imagesTr\liver_91.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_91
✅ liver_91.nii.gz converted: 751 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_91
Processing D:\\Task03_Liver\\imagesTr\liver_92.nii.gz --> D:\\Task03_Liver\\dicomm_files\\images\liver_92
✅ liver_92.nii.gz converted: 836 DICOM slices saved to D:\\Task03_Liver\\dicomm_files\\images\liver_92
Processing D:\\Task03_Liver\\imagesTr\liver_93.nii.gz --> D:\\Tas

# NIFTI TO DICOM (LABELS)

In [30]:
import os
import glob
import nibabel as nib
import numpy as np
import pydicom
from pydicom.dataset import Dataset, FileDataset
import datetime

def nifti_to_dicom(nifti_path, dicom_output_path):
    """
    Convert a NIfTI label file to DICOM slices and save in dicom_output_path.
    """
    # Load NIfTI image
    nii_img = nib.load(nifti_path)
    data = nii_img.get_fdata()  # Get image data as a numpy array
    dims = data.shape  # Shape of the NIfTI image

    # Create output folder
    os.makedirs(dicom_output_path, exist_ok=True)

    # Iterate through each slice along the Z-axis
    for i in range(dims[2]):  # Third dimension is slices
        slice_data = data[:, :, i]

        # Convert labels to uint16 to preserve full integer values
        slice_data_uint16 = slice_data.astype(np.uint16)

        # Create DICOM dataset
        file_meta = Dataset()
        ds = FileDataset(None, {}, file_meta=file_meta, preamble=b"\0" * 128)

        # Set metadata
        ds.PatientName = "Liver_Label"
        ds.PatientID = os.path.basename(nifti_path).split(".")[0]
        ds.Modality = "SEG"  # Label data modality
        ds.StudyInstanceUID = pydicom.uid.generate_uid()
        ds.SeriesInstanceUID = pydicom.uid.generate_uid()
        ds.SOPInstanceUID = pydicom.uid.generate_uid()
        ds.StudyDate = datetime.datetime.now().strftime("%Y%m%d")
        ds.ContentDate = datetime.datetime.now().strftime("%Y%m%d")
        ds.ContentTime = datetime.datetime.now().strftime("%H%M%S")
        ds.Rows, ds.Columns = slice_data.shape

        # Pixel Data
        ds.SamplesPerPixel = 1
        ds.PhotometricInterpretation = "MONOCHROME2"
        ds.PixelRepresentation = 1  # Unsigned integer
        ds.BitsAllocated = 16
        ds.BitsStored = 16
        ds.HighBit = 15
        ds.PixelData = slice_data_uint16.tobytes()

        # Save as DICOM file
        dicom_file_path = os.path.join(dicom_output_path, f"slice_{i:03d}.dcm")
        ds.save_as(dicom_file_path)
        print(f"Saved slice {i} as DICOM: {dicom_file_path}")

def process_labels_directory(input_root, output_root):
    """
    Process all NIfTI label files found inside the input_root directory.
    Convert them into DICOM slices and store them in corresponding output folders.
    """
    # Find all NIfTI files
    nifti_files = glob.glob(os.path.join(input_root, "*.nii*"))
    print(f"Found {len(nifti_files)} NIfTI label files.")

    # Process each NIfTI file
    for nifti_file in nifti_files:
        file_name = os.path.basename(nifti_file).split(".")[0]  # Extract file name without extension
        dicom_folder = os.path.join(output_root, file_name)  # Create respective output folder
        print(f"Processing {nifti_file} --> {dicom_folder}")

        nifti_to_dicom(nifti_file, dicom_folder)

    print("🎯🎯🎯🎯All label files processed.")

# Set paths
input_labels_dir = r"D:\\Task03_Liver\\labelsTr"  # Path where NIfTI label files are stored
output_labels_dir = r"D:\\Task03_Liver\\dicomm_files\\labels"  # Output folder for DICOM label files

# Run conversion
process_labels_directory(input_labels_dir, output_labels_dir)


Found 131 NIfTI label files.
Processing D:\\Task03_Liver\\labelsTr\liver_0.nii.gz --> D:\\Task03_Liver\\dicomm_files\\labels\liver_0
Saved slice 0 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_000.dcm
Saved slice 1 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_001.dcm
Saved slice 2 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_002.dcm
Saved slice 3 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_003.dcm
Saved slice 4 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_004.dcm
Saved slice 5 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_005.dcm
Saved slice 6 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_006.dcm
Saved slice 7 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_007.dcm
Saved slice 8 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_008.dcm
Saved slice 9 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_0\slice_009.dcm
Saved slice 10 as

Saved slice 19 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_019.dcm
Saved slice 20 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_020.dcm
Saved slice 21 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_021.dcm
Saved slice 22 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_022.dcm
Saved slice 23 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_023.dcm
Saved slice 24 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_024.dcm
Saved slice 25 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_025.dcm
Saved slice 26 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_026.dcm
Saved slice 27 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_027.dcm
Saved slice 28 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_028.dcm
Saved slice 29 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_029.dcm
Saved slice 30 as DICOM: D:\\Task03_Liver\\dicomm_file

Saved slice 119 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_119.dcm
Saved slice 120 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_120.dcm
Saved slice 121 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_121.dcm
Saved slice 122 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_1\slice_122.dcm
Processing D:\\Task03_Liver\\labelsTr\liver_10.nii.gz --> D:\\Task03_Liver\\dicomm_files\\labels\liver_10
Saved slice 0 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_000.dcm
Saved slice 1 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_001.dcm
Saved slice 2 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_002.dcm
Saved slice 3 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_003.dcm
Saved slice 4 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_004.dcm
Saved slice 5 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_005.dcm
Saved slice 6 as DICOM: D:\\Ta

Saved slice 104 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_104.dcm
Saved slice 105 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_105.dcm
Saved slice 106 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_106.dcm
Saved slice 107 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_107.dcm
Saved slice 108 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_108.dcm
Saved slice 109 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_109.dcm
Saved slice 110 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_110.dcm
Saved slice 111 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_111.dcm
Saved slice 112 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_112.dcm
Saved slice 113 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_113.dcm
Saved slice 114 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_114.dcm
Saved slice 115 as DICOM: D:\\Ta

Saved slice 218 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_218.dcm
Saved slice 219 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_219.dcm
Saved slice 220 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_220.dcm
Saved slice 221 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_221.dcm
Saved slice 222 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_222.dcm
Saved slice 223 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_223.dcm
Saved slice 224 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_224.dcm
Saved slice 225 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_225.dcm
Saved slice 226 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_226.dcm
Saved slice 227 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_227.dcm
Saved slice 228 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_10\slice_228.dcm
Saved slice 229 as DICOM: D:\\Ta

...

Saved slice 176 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_176.dcm
Saved slice 177 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_177.dcm
Saved slice 178 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_178.dcm
Saved slice 179 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_179.dcm
Saved slice 180 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_180.dcm
Saved slice 181 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_181.dcm
Saved slice 182 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_182.dcm
Saved slice 183 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_183.dcm
Saved slice 184 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_184.dcm
Saved slice 185 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_185.dcm
Saved slice 186 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_186.dcm
Saved slice 187 as DICOM: D:\\Ta

Saved slice 283 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_283.dcm
Saved slice 284 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_284.dcm
Saved slice 285 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_285.dcm
Saved slice 286 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_286.dcm
Saved slice 287 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_287.dcm
Saved slice 288 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_288.dcm
Saved slice 289 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_289.dcm
Saved slice 290 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_290.dcm
Saved slice 291 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_291.dcm
Saved slice 292 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_292.dcm
Saved slice 293 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_293.dcm
Saved slice 294 as DICOM: D:\\Ta

Saved slice 387 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_387.dcm
Saved slice 388 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_388.dcm
Saved slice 389 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_389.dcm
Saved slice 390 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_390.dcm
Saved slice 391 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_391.dcm
Saved slice 392 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_392.dcm
Saved slice 393 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_393.dcm
Saved slice 394 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_394.dcm
Saved slice 395 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_395.dcm
Saved slice 396 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_396.dcm
Saved slice 397 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_397.dcm
Saved slice 398 as DICOM: D:\\Ta

Saved slice 486 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_486.dcm
Saved slice 487 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_487.dcm
Saved slice 488 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_488.dcm
Saved slice 489 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_489.dcm
Saved slice 490 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_490.dcm
Saved slice 491 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_491.dcm
Saved slice 492 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_492.dcm
Saved slice 493 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_493.dcm
Saved slice 494 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_494.dcm
Saved slice 495 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_495.dcm
Saved slice 496 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_496.dcm
Saved slice 497 as DICOM: D:\\Ta

Saved slice 584 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_584.dcm
Saved slice 585 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_585.dcm
Saved slice 586 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_586.dcm
Saved slice 587 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_587.dcm
Saved slice 588 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_588.dcm
Saved slice 589 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_589.dcm
Saved slice 590 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_590.dcm
Saved slice 591 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_591.dcm
Saved slice 592 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_592.dcm
Saved slice 593 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_593.dcm
Saved slice 594 as DICOM: D:\\Task03_Liver\\dicomm_files\\labels\liver_99\slice_594.dcm
Saved slice 595 as DICOM: D:\\Ta

# GROUPING OF DICOM SLICES (LABELS)

In [17]:
import os
import shutil
import glob
import pydicom


def fix_dicom_metadata(dicom_path):
    """Ensure all DICOM files have valid InstanceNumber and required metadata."""
    for dicom_file in glob.glob(os.path.join(dicom_path, "*.dcm")):
        ds = pydicom.dcmread(dicom_file)

        # Ensure InstanceNumber exists
        if not hasattr(ds, "InstanceNumber") or ds.InstanceNumber is None:
            ds.InstanceNumber = int(os.path.basename(dicom_file).split('_')[-1].split('.')[0])

        # Add essential metadata
        ds.SliceThickness = 1.0
        ds.PixelSpacing = [1.0, 1.0]
        ds.ImagePositionPatient = [0, 0, ds.InstanceNumber]

        # Save fixed file
        ds.save_as(dicom_file)

    print(f"✅ Fixed metadata for all DICOM files in {dicom_path}")


# Define input and output paths
in_path = r'D:\Task03_Liver\dicomm_files\labels'
out_path = r'D:\Task03_Liver\dicomm_groups\labels'

# Process each patient folder
for patient in glob.glob(os.path.join(in_path, '*')):
    patient_name = os.path.basename(os.path.normpath(patient))

    # Get all slice files
    slice_files = glob.glob(os.path.join(patient, '*.dcm'))

    if not slice_files:
        print(f"⚠ No DICOM files found in {patient_name}")
        continue

    # Fix metadata before sorting
    fix_dicom_metadata(patient)

    # Read and sort DICOM files by InstanceNumber
    dicom_slices = []
    for f in slice_files:
        ds = pydicom.dcmread(f)
        instance_number = getattr(ds, "InstanceNumber", None)
        if instance_number is None:
            instance_number = int(os.path.basename(f).split('_')[-1].split('.')[0])
            ds.InstanceNumber = instance_number
            ds.save_as(f)  # Save with updated InstanceNumber
        dicom_slices.append((f, instance_number))

    dicom_slices.sort(key=lambda x: x[1])  # Sort by InstanceNumber

    # Extract sorted filenames
    sorted_files = [f[0] for f in dicom_slices]
    total_slices = len(sorted_files)

    # Determine the number of folders required
    number_folders = (total_slices + 63) // 64  # Ensures all slices are included

    print(f"📂 Processing {patient_name} with {total_slices} slices into {number_folders} folders")

    # Move slices into respective folders
    for folder_idx in range(number_folders):
        output_folder = os.path.join(out_path, f"{patient_name}_{folder_idx}")
        os.makedirs(output_folder, exist_ok=True)

        # Select slices for this folder
        start_idx = folder_idx * 64
        end_idx = min(start_idx + 64, total_slices)

        for i in range(start_idx, end_idx):
            shutil.move(sorted_files[i], output_folder)

    print(f"✅ Completed {patient_name}")


Processing liver_0 with 0 slices into 0 folders
✅ Completed liver_0
Processing liver_1 with 0 slices into 0 folders
✅ Completed liver_1
Processing liver_10 with 371 slices into 6 folders
✅ Completed liver_10
Processing liver_100 with 555 slices into 9 folders
✅ Completed liver_100
Processing liver_101 with 553 slices into 9 folders
✅ Completed liver_101
Processing liver_102 with 547 slices into 9 folders
✅ Completed liver_102
Processing liver_103 with 553 slices into 9 folders
✅ Completed liver_103
Processing liver_104 with 651 slices into 11 folders
✅ Completed liver_104
Processing liver_105 with 856 slices into 14 folders
✅ Completed liver_105
Processing liver_106 with 641 slices into 11 folders
✅ Completed liver_106
Processing liver_107 with 641 slices into 11 folders
✅ Completed liver_107
Processing liver_108 with 726 slices into 12 folders
✅ Completed liver_108
Processing liver_109 with 626 slices into 10 folders
✅ Completed liver_109
Processing liver_11 with 336 slices into 6 fol

✅ Completed liver_84
Processing liver_85 with 500 slices into 8 folders
✅ Completed liver_85
Processing liver_86 with 517 slices into 9 folders
✅ Completed liver_86
Processing liver_87 with 766 slices into 12 folders
✅ Completed liver_87
Processing liver_88 with 681 slices into 11 folders
✅ Completed liver_88
Processing liver_89 with 636 slices into 10 folders
✅ Completed liver_89
Processing liver_9 with 419 slices into 7 folders
✅ Completed liver_9
Processing liver_90 with 621 slices into 10 folders
✅ Completed liver_90
Processing liver_91 with 621 slices into 10 folders
✅ Completed liver_91
Processing liver_92 with 706 slices into 12 folders
✅ Completed liver_92
Processing liver_93 with 566 slices into 9 folders
✅ Completed liver_93
Processing liver_94 with 787 slices into 13 folders
✅ Completed liver_94
Processing liver_95 with 711 slices into 12 folders
✅ Completed liver_95
Processing liver_96 with 592 slices into 10 folders
✅ Completed liver_96
Processing liver_97 with 541 slices 

# GROUPING OF DICOM SLICES (IMAGES)

In [18]:
in_path='D:\Task03_Liver\dicomm_files\images'
out_path='D:\Task03_Liver\dicomm_groups\images'

In [19]:
# Process each patient folder
for patient in glob(os.path.join(in_path, '*')):
    patient_name = os.path.basename(os.path.normpath(patient))
    
    # Get all slice files for this patient
    slice_files = sorted(glob(os.path.join(patient, '*')))  # Sorting ensures order is maintained
    total_slices = len(slice_files)

    # Determine how many folders to create
    number_folders = (total_slices + 63) // 64  # Ensures all slices are included

    print(f"Processing {patient_name} with {total_slices} slices into {number_folders} folders")

    # Move slices into respective folders
    for folder_idx in range(number_folders):
        output_folder = os.path.join(out_path, f"{patient_name}_{folder_idx}")
        os.makedirs(output_folder, exist_ok=True)

        # Select slices for this folder
        start_idx = folder_idx * 64
        end_idx = min(start_idx + 64, total_slices)

        for i in range(start_idx, end_idx):
            shutil.move(slice_files[i], output_folder)
    
    print(f"✅ Completed {patient_name}")


Processing liver_0 with 75 slices into 2 folders
✅ Completed liver_0
Processing liver_1 with 123 slices into 2 folders
✅ Completed liver_1
Processing liver_10 with 501 slices into 8 folders
✅ Completed liver_10
Processing liver_100 with 685 slices into 11 folders
✅ Completed liver_100
Processing liver_101 with 683 slices into 11 folders
✅ Completed liver_101
Processing liver_102 with 677 slices into 11 folders
✅ Completed liver_102
Processing liver_103 with 683 slices into 11 folders
✅ Completed liver_103
Processing liver_104 with 781 slices into 13 folders
✅ Completed liver_104
Processing liver_105 with 986 slices into 16 folders
✅ Completed liver_105
Processing liver_106 with 771 slices into 13 folders
✅ Completed liver_106
Processing liver_107 with 771 slices into 13 folders
✅ Completed liver_107
Processing liver_108 with 856 slices into 14 folders
✅ Completed liver_108
Processing liver_109 with 756 slices into 12 folders
✅ Completed liver_109
Processing liver_11 with 466 slices int

Processing liver_83 with 871 slices into 14 folders
✅ Completed liver_83
Processing liver_84 with 733 slices into 12 folders
✅ Completed liver_84
Processing liver_85 with 630 slices into 10 folders
✅ Completed liver_85
Processing liver_86 with 647 slices into 11 folders
✅ Completed liver_86
Processing liver_87 with 896 slices into 14 folders
✅ Completed liver_87
Processing liver_88 with 811 slices into 13 folders
✅ Completed liver_88
Processing liver_89 with 766 slices into 12 folders
✅ Completed liver_89
Processing liver_9 with 549 slices into 9 folders
✅ Completed liver_9
Processing liver_90 with 751 slices into 12 folders
✅ Completed liver_90
Processing liver_91 with 751 slices into 12 folders
✅ Completed liver_91
Processing liver_92 with 836 slices into 14 folders
✅ Completed liver_92
Processing liver_93 with 696 slices into 11 folders
✅ Completed liver_93
Processing liver_94 with 917 slices into 15 folders
✅ Completed liver_94
Processing liver_95 with 841 slices into 14 folders
✅ 

In [28]:
in_path_images='D:\Task03_Liver\dicomm_groups\images\*'
in_path_labels='D:\Task03_Liver\dicomm_groups\labels\*'
out_path_images='D:\Task03_Liver\nifti_files\images'
out_path_labels='D:\Task03_Liver\nifti_files\labels'
list_images=glob(in_path_images)
list_labels=glob(in_path_labels)

In [25]:
import pydicom
from glob import glob

# Load one file and check metadata
dicom_files = glob('D:/Task03_Liver/dicomm_groups/images/*/*')  # Adjust path
if dicom_files:
    ds = pydicom.dcmread(dicom_files[0], force=True)  # Force-read to ignore missing meta
    print(ds)
else:
    print("No DICOM files found.")


(0008, 0018) SOP Instance UID                    UI: 1.2.826.0.1.3680043.8.498.48814119725683384003997725705617485169
(0008, 0020) Study Date                          DA: '20250130'
(0008, 0023) Content Date                        DA: '20250130'
(0008, 0033) Content Time                        TM: '112804'
(0008, 0060) Modality                            CS: 'CT'
(0010, 0010) Patient's Name                      PN: 'Liver_Patient'
(0010, 0020) Patient ID                          LO: 'liver_0'
(0018, 0050) Slice Thickness                     DS: '1.0'
(0020, 000d) Study Instance UID                  UI: 1.2.826.0.1.3680043.8.498.16265275186265378552573952050045606496
(0020, 000e) Series Instance UID                 UI: 1.2.826.0.1.3680043.8.498.54722542780571147620833973342700972952
(0020, 0013) Instance Number                     IS: '1'
(0020, 0032) Image Position (Patient)            DS: [0.0, 0.0, 0.0]
(0020, 0037) Image Orientation (Patient)         DS: [1.0, 0.0, 0.0, 0.0, 1.0, 0.

# CONVERTING GROUPED DICOM SLICES SERIES BACK TO NIFTI (IMAGES)

In [ ]:
import os
import dicom2nifti
from glob import glob
import pydicom
from pydicom.dataset import Dataset, FileDataset
import datetime

# Input & Output Paths
in_path_images = r"D:\Task03_Liver\dicomm_groups\images\*"
out_path_images = r"D:\Task03_Liver\nifti_files\images"


# Get List of DICOM Series
list_images = glob(in_path_images)
list_labels = glob(in_path_labels)

# Ensure output directories exist
os.makedirs(out_path_images, exist_ok=True)
os.makedirs(out_path_labels, exist_ok=True)

# Function to fix metadata
def fix_dicom_metadata(dicom_path):
    """Ensure DICOM files have necessary metadata"""
    for dicom_file in glob(os.path.join(dicom_path, "*.dcm")):
        ds = pydicom.dcmread(dicom_file)
        
        # Ensure TransferSyntaxUID is set
        if not hasattr(ds.file_meta, "TransferSyntaxUID"):
            ds.file_meta.TransferSyntaxUID = pydicom.uid.ImplicitVRLittleEndian
        
        # Save fixed file
        ds.save_as(dicom_file)

# Convert DICOM to NIfTI
def convert_dicom_to_nifti(input_path, output_path):
    for patient in input_path:
        patient_name = os.path.basename(os.path.normpath(patient))
        try:
            print(f"Processing: {patient}")
            fix_dicom_metadata(patient)  # Fix metadata before conversion
            dicom2nifti.dicom_series_to_nifti(patient, os.path.join(output_path, f"{patient_name}.nii.gz"))
            print(f"Converted {patient_name} to NIfTI.")
        except Exception as e:
            print(f"Error converting {patient_name}: {e}")

# Run conversion for images and labels
convert_dicom_to_nifti(list_images, out_path_images)



Processing: D:\Task03_Liver\dicomm_groups\images\liver_0_0
Converted liver_0_0 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_0_1
Converted liver_0_1 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_0
Converted liver_100_0 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_1
Converted liver_100_1 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_10
Converted liver_100_10 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_2
Converted liver_100_2 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_3
Converted liver_100_3 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_4
Converted liver_100_4 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_5
Converted liver_100_5 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_6
Converted liver_100_6 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_100_7
Converted liver

At least 3 slices are needed for correct conversion
---------------------------------------------------------


Converted liver_106_11 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_12
Error converting liver_106_12: TOO_FEW_SLICES/LOCALIZER
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_2
Converted liver_106_2 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_3
Converted liver_106_3 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_4
Converted liver_106_4 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_5
Converted liver_106_5 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_6
Converted liver_106_6 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_7
Converted liver_106_7 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_8
Converted liver_106_8 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_106_9
Converted liver_106_9 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_0
Converted liver_107_0 to NIfTI.
Processing: 

At least 3 slices are needed for correct conversion
---------------------------------------------------------


Error converting liver_107_12: TOO_FEW_SLICES/LOCALIZER
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_2
Converted liver_107_2 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_3
Converted liver_107_3 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_4
Converted liver_107_4 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_5
Converted liver_107_5 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_6
Converted liver_107_6 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_7
Converted liver_107_7 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_8
Converted liver_107_8 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_107_9
Converted liver_107_9 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_108_0
Converted liver_108_0 to NIfTI.
Processing: D:\Task03_Liver\dicomm_groups\images\liver_108_1
Converted liver_108_1 to NIfTI.
Processing: D:

...

Error converting liver_116_6: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_116_7
Error converting liver_116_7: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_116_8
Error converting liver_116_8: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_116_9
Error converting liver_116_9: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_117_0
Error converting liver_117_0: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_117_1
Error converting liver_117_1: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_117_10
Error converting liver_117_10: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_117_11
Error converting liver_117_11: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_117_2
Error converting liver_117_2: list index out of range
Processing: D:\Task03_

Error converting liver_127_11: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_127_12
Error converting liver_127_12: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_127_13
Error converting liver_127_13: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_127_2
Error converting liver_127_2: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_127_3
Error converting liver_127_3: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_127_4
Error converting liver_127_4: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_127_5
Error converting liver_127_5: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_127_6
Error converting liver_127_6: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_127_7
Error converting liver_127_7: list index out of range
Processing: D:\Task03

Error converting liver_17_10: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_17_2
Error converting liver_17_2: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_17_3
Error converting liver_17_3: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_17_4
Error converting liver_17_4: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_17_5
Error converting liver_17_5: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_17_6
Error converting liver_17_6: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_17_7
Error converting liver_17_7: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_17_8
Error converting liver_17_8: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_17_9
Error converting liver_17_9: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\

Error converting liver_27_4: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_27_5
Error converting liver_27_5: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_27_6
Error converting liver_27_6: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_27_7
Error converting liver_27_7: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_27_8
Error converting liver_27_8: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_27_9
Error converting liver_27_9: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_29_0
Error converting liver_29_0: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_2_0
Error converting liver_2_0: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_2_1
Error converting liver_2_1: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\label

Error converting liver_60_1: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_61_0
Error converting liver_61_0: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_62_0
Error converting liver_62_0: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_64_0
Error converting liver_64_0: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_64_1
Error converting liver_64_1: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_65_0
Error converting liver_65_0: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_65_1
Error converting liver_65_1: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_65_2
Error converting liver_65_2: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\labels\liver_65_3
Error converting liver_65_3: list index out of range
Processing: D:\Task03_Liver\dicomm_groups\l

#  CONVERTING GROUPED DICOM SLICES SERIES BACK TO NIFTI (LABELS)

In [1]:
import SimpleITK as sitk
import os

dicom_root = r"D:\Task03_Liver\dicomm_groups\labels"
output_root = r"D:\Task03_Liver\nifti_files\labels"

os.makedirs(output_root, exist_ok=True)

for patient_folder in os.listdir(dicom_root):
    dicom_path = os.path.join(dicom_root, patient_folder)
    
    if not os.path.isdir(dicom_path):
        continue  

    reader = sitk.ImageSeriesReader()
    series_ids = reader.GetGDCMSeriesIDs(dicom_path)

    if not series_ids:
        print(f"❌ Skipping {patient_folder}: No valid DICOM series found.")
        continue

    dicom_series = []
    for series_id in series_ids:
        dicom_series.extend(reader.GetGDCMSeriesFileNames(dicom_path, series_id))

    if len(dicom_series) < 64:
        print(f"⚠ Warning: {patient_folder} has {len(dicom_series)} slices instead of 64.")

    # Sort slices based on metadata before loading
    dicom_series = sorted(dicom_series, key=lambda x: int(pydicom.dcmread(x).InstanceNumber))

    reader.SetFileNames(dicom_series)
    image = reader.Execute()

    output_path = os.path.join(output_root, f"{patient_folder}.nii.gz")
    sitk.WriteImage(image, output_path)

    print(f"✅ Successfully converted {patient_folder} ({len(dicom_series)} slices) to NIfTI: {output_path}")


Converted liver_100_0 -> D:\Task03_Liver\nifti_files\labels\liver_100_0.nii.gz
Converted liver_100_1 -> D:\Task03_Liver\nifti_files\labels\liver_100_1.nii.gz
Converted liver_100_2 -> D:\Task03_Liver\nifti_files\labels\liver_100_2.nii.gz
Converted liver_100_3 -> D:\Task03_Liver\nifti_files\labels\liver_100_3.nii.gz
Converted liver_100_4 -> D:\Task03_Liver\nifti_files\labels\liver_100_4.nii.gz
Converted liver_100_5 -> D:\Task03_Liver\nifti_files\labels\liver_100_5.nii.gz
Converted liver_100_6 -> D:\Task03_Liver\nifti_files\labels\liver_100_6.nii.gz
Converted liver_100_7 -> D:\Task03_Liver\nifti_files\labels\liver_100_7.nii.gz
Converted liver_100_8 -> D:\Task03_Liver\nifti_files\labels\liver_100_8.nii.gz
Converted liver_101_0 -> D:\Task03_Liver\nifti_files\labels\liver_101_0.nii.gz
Converted liver_101_1 -> D:\Task03_Liver\nifti_files\labels\liver_101_1.nii.gz
Converted liver_101_2 -> D:\Task03_Liver\nifti_files\labels\liver_101_2.nii.gz
Converted liver_101_3 -> D:\Task03_Liver\nifti_files

Converted liver_109_9 -> D:\Task03_Liver\nifti_files\labels\liver_109_9.nii.gz
Converted liver_10_0 -> D:\Task03_Liver\nifti_files\labels\liver_10_0.nii.gz
Converted liver_10_1 -> D:\Task03_Liver\nifti_files\labels\liver_10_1.nii.gz
Converted liver_10_2 -> D:\Task03_Liver\nifti_files\labels\liver_10_2.nii.gz
Converted liver_10_3 -> D:\Task03_Liver\nifti_files\labels\liver_10_3.nii.gz
Converted liver_10_4 -> D:\Task03_Liver\nifti_files\labels\liver_10_4.nii.gz
Converted liver_10_5 -> D:\Task03_Liver\nifti_files\labels\liver_10_5.nii.gz
Converted liver_110_0 -> D:\Task03_Liver\nifti_files\labels\liver_110_0.nii.gz
Converted liver_110_1 -> D:\Task03_Liver\nifti_files\labels\liver_110_1.nii.gz
Converted liver_110_10 -> D:\Task03_Liver\nifti_files\labels\liver_110_10.nii.gz
Converted liver_110_2 -> D:\Task03_Liver\nifti_files\labels\liver_110_2.nii.gz
Converted liver_110_3 -> D:\Task03_Liver\nifti_files\labels\liver_110_3.nii.gz
Converted liver_110_4 -> D:\Task03_Liver\nifti_files\labels\li

Converted liver_119_0 -> D:\Task03_Liver\nifti_files\labels\liver_119_0.nii.gz
Converted liver_119_1 -> D:\Task03_Liver\nifti_files\labels\liver_119_1.nii.gz
Converted liver_119_2 -> D:\Task03_Liver\nifti_files\labels\liver_119_2.nii.gz
Converted liver_119_3 -> D:\Task03_Liver\nifti_files\labels\liver_119_3.nii.gz
Converted liver_119_4 -> D:\Task03_Liver\nifti_files\labels\liver_119_4.nii.gz
Converted liver_119_5 -> D:\Task03_Liver\nifti_files\labels\liver_119_5.nii.gz
Converted liver_11_0 -> D:\Task03_Liver\nifti_files\labels\liver_11_0.nii.gz
Converted liver_11_1 -> D:\Task03_Liver\nifti_files\labels\liver_11_1.nii.gz
Converted liver_11_2 -> D:\Task03_Liver\nifti_files\labels\liver_11_2.nii.gz
Converted liver_11_3 -> D:\Task03_Liver\nifti_files\labels\liver_11_3.nii.gz
Converted liver_11_4 -> D:\Task03_Liver\nifti_files\labels\liver_11_4.nii.gz
Converted liver_11_5 -> D:\Task03_Liver\nifti_files\labels\liver_11_5.nii.gz
Converted liver_120_0 -> D:\Task03_Liver\nifti_files\labels\live

Converted liver_15_0 -> D:\Task03_Liver\nifti_files\labels\liver_15_0.nii.gz
Converted liver_15_1 -> D:\Task03_Liver\nifti_files\labels\liver_15_1.nii.gz
Converted liver_15_2 -> D:\Task03_Liver\nifti_files\labels\liver_15_2.nii.gz
Converted liver_15_3 -> D:\Task03_Liver\nifti_files\labels\liver_15_3.nii.gz
Converted liver_15_4 -> D:\Task03_Liver\nifti_files\labels\liver_15_4.nii.gz
Converted liver_15_5 -> D:\Task03_Liver\nifti_files\labels\liver_15_5.nii.gz
Converted liver_15_6 -> D:\Task03_Liver\nifti_files\labels\liver_15_6.nii.gz
Converted liver_16_0 -> D:\Task03_Liver\nifti_files\labels\liver_16_0.nii.gz
Converted liver_16_1 -> D:\Task03_Liver\nifti_files\labels\liver_16_1.nii.gz
Converted liver_16_2 -> D:\Task03_Liver\nifti_files\labels\liver_16_2.nii.gz
Converted liver_16_3 -> D:\Task03_Liver\nifti_files\labels\liver_16_3.nii.gz
Converted liver_16_4 -> D:\Task03_Liver\nifti_files\labels\liver_16_4.nii.gz
Converted liver_16_5 -> D:\Task03_Liver\nifti_files\labels\liver_16_5.nii.gz

Converted liver_32_0 -> D:\Task03_Liver\nifti_files\labels\liver_32_0.nii.gz
Converted liver_33_0 -> D:\Task03_Liver\nifti_files\labels\liver_33_0.nii.gz
Converted liver_34_0 -> D:\Task03_Liver\nifti_files\labels\liver_34_0.nii.gz
Converted liver_38_0 -> D:\Task03_Liver\nifti_files\labels\liver_38_0.nii.gz
Converted liver_39_0 -> D:\Task03_Liver\nifti_files\labels\liver_39_0.nii.gz
Converted liver_39_1 -> D:\Task03_Liver\nifti_files\labels\liver_39_1.nii.gz
Converted liver_39_2 -> D:\Task03_Liver\nifti_files\labels\liver_39_2.nii.gz
Converted liver_3_0 -> D:\Task03_Liver\nifti_files\labels\liver_3_0.nii.gz
Converted liver_3_1 -> D:\Task03_Liver\nifti_files\labels\liver_3_1.nii.gz
Converted liver_3_2 -> D:\Task03_Liver\nifti_files\labels\liver_3_2.nii.gz
Converted liver_3_3 -> D:\Task03_Liver\nifti_files\labels\liver_3_3.nii.gz
Converted liver_3_4 -> D:\Task03_Liver\nifti_files\labels\liver_3_4.nii.gz
Converted liver_3_5 -> D:\Task03_Liver\nifti_files\labels\liver_3_5.nii.gz
Converted l

Converted liver_82_5 -> D:\Task03_Liver\nifti_files\labels\liver_82_5.nii.gz
Converted liver_82_6 -> D:\Task03_Liver\nifti_files\labels\liver_82_6.nii.gz
Converted liver_83_0 -> D:\Task03_Liver\nifti_files\labels\liver_83_0.nii.gz
Converted liver_83_1 -> D:\Task03_Liver\nifti_files\labels\liver_83_1.nii.gz
Converted liver_83_10 -> D:\Task03_Liver\nifti_files\labels\liver_83_10.nii.gz
Converted liver_83_11 -> D:\Task03_Liver\nifti_files\labels\liver_83_11.nii.gz
Converted liver_83_2 -> D:\Task03_Liver\nifti_files\labels\liver_83_2.nii.gz
Converted liver_83_3 -> D:\Task03_Liver\nifti_files\labels\liver_83_3.nii.gz
Converted liver_83_4 -> D:\Task03_Liver\nifti_files\labels\liver_83_4.nii.gz
Converted liver_83_5 -> D:\Task03_Liver\nifti_files\labels\liver_83_5.nii.gz
Converted liver_83_6 -> D:\Task03_Liver\nifti_files\labels\liver_83_6.nii.gz
Converted liver_83_7 -> D:\Task03_Liver\nifti_files\labels\liver_83_7.nii.gz
Converted liver_83_8 -> D:\Task03_Liver\nifti_files\labels\liver_83_8.ni

Converted liver_92_4 -> D:\Task03_Liver\nifti_files\labels\liver_92_4.nii.gz
Converted liver_92_5 -> D:\Task03_Liver\nifti_files\labels\liver_92_5.nii.gz
Converted liver_92_6 -> D:\Task03_Liver\nifti_files\labels\liver_92_6.nii.gz
Converted liver_92_7 -> D:\Task03_Liver\nifti_files\labels\liver_92_7.nii.gz
Converted liver_92_8 -> D:\Task03_Liver\nifti_files\labels\liver_92_8.nii.gz
Converted liver_92_9 -> D:\Task03_Liver\nifti_files\labels\liver_92_9.nii.gz
Converted liver_93_0 -> D:\Task03_Liver\nifti_files\labels\liver_93_0.nii.gz
Converted liver_93_1 -> D:\Task03_Liver\nifti_files\labels\liver_93_1.nii.gz
Converted liver_93_2 -> D:\Task03_Liver\nifti_files\labels\liver_93_2.nii.gz
Converted liver_93_3 -> D:\Task03_Liver\nifti_files\labels\liver_93_3.nii.gz
Converted liver_93_4 -> D:\Task03_Liver\nifti_files\labels\liver_93_4.nii.gz
Converted liver_93_5 -> D:\Task03_Liver\nifti_files\labels\liver_93_5.nii.gz
Converted liver_93_6 -> D:\Task03_Liver\nifti_files\labels\liver_93_6.nii.gz